In [10]:
import glob
import argparse
import os
import time
import sys
import tensorflow as tf
from itertools import count
from config import cfg
from model import RPN3D
from utils import *
from utils.kitti_loader import iterate_data, sample_test_data
from train_hook import check_if_should_pause






dataset_dir = cfg.DATA_DIR
train_dir = os.path.join(cfg.DATA_DIR, 'training')
val_dir = os.path.join(cfg.DATA_DIR, 'validation')
log_dir = os.path.join('./log',tag)
save_model_dir = os.path.join('./save_model', tag)
os.makedirs(log_dir, exist_ok=True)
os.makedirs(save_model_dir, exist_ok=True)


In [ ]:
#Configuration variables
loss = 'original' #original or focal loss
tag = "jupyter" # Tag to be used for experiment 
bs = 2 # Batch size
alpha=0.25 #alpha value for loss(both original and focal)
beta =2 # beta value for original loss 
gamma = 2 # gamma value for focal loss 
lr = 0.001 # learning rate 
epochs=160 # number of epochs
vis= True # visualisation dumping
output_path="./predictions/jupyter_alpha.25_gamma_2" # path to dump predictions

In [ ]:


mem_fraction=cfg.GPU_MEMORY_FRACTION
# TODO: split file support
with tf.Graph().as_default():
    global save_model_dir
    start_epoch = 0
    global_counter = 0

    gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=mem_fraction,
                                visible_device_list=cfg.GPU_AVAILABLE,
                                allow_growth=True)
    config = tf.ConfigProto(
        gpu_options=gpu_options,
        device_count={
            "GPU": cfg.GPU_USE_COUNT,
        },
    allow_soft_placement=True,
        log_device_placement=False,
    )
    with tf.Session(config=config) as sess:

        model = RPN3D(
            cls=cfg.DETECT_OBJ,
            single_batch_size=bs,
            learning_rate=lr,
            max_gradient_norm=5.0,
            alpha=alpha,
            beta=beta,
            gamma = gamma,
            loss_type=loss
            avail_gpus=cfg.GPU_AVAILABLE.split(',')
        )
        
        
        # param init/restore
        if tf.train.get_checkpoint_state(save_model_dir):
            print("Reading model parameters from %s" % save_model_dir)
            model.saver.restore(
                sess, tf.train.latest_checkpoint(save_model_dir))
            start_epoch = model.epoch.eval() + 1
            global_counter = model.global_step.eval() + 1
        else:
            print("Created model with fresh parameters.")
            tf.global_variables_initializer().run()

        # train and validate
        is_summary, is_summary_image, is_validate = False, False, False

        summary_interval = 5
        summary_val_interval = 10
        summary_writer = tf.summary.FileWriter(log_dir, sess.graph)
        
#         experiment.set_model_graph(sess.graph)

#         variables_names = [v.name for v in tf.trainable_variables()]
#         values = sess.run(variables_names)
# #         for k, v in zip(variables_names, values): #t
# #             print("Variable: ", k)
# #             print ("Shape: ", v.shape)
# #             print (v)
        # training
#         with experiment.train():
        for epoch in range(start_epoch, epochs):
            counter = 0
            batch_time = time.time()
#             experiment.log_current_epoch(epoch)

            for batch in iterate_data(train_dir, shuffle=True, aug=True, is_testset=False, batch_size=bs * cfg.GPU_USE_COUNT, multi_gpu_sum=cfg.GPU_USE_COUNT):

                counter += 1
                global_counter += 1
#                 experiment.set_step(global_counter)
                if counter % summary_interval == 0:
                    is_summary = True
                else:
                    is_summary = False

                start_time = time.time()
                ret = model.train_step( sess, batch, train=True, summary = is_summary )
                forward_time = time.time() - start_time
                batch_time = time.time() - batch_time
                param=ret
#                     params={"loss": param[0], "cls_loss": param[1],"cls_pos_loss":param[2],"cls_neg_loss":param[3],"focal_loss": param[7]}
#                     experiment.log_multiple_metrics(params)

                print('train: {} @ epoch:{}/{} loss: {:.4f} cls_loss: {:.4f} cls_pos_loss: {:.4f} cls_neg_loss: {:.4f} forward time: {:.4f} batch time: {:.4f}'.format(counter,epoch, epochs, ret[0], ret[1], ret[2], ret[3], forward_time, batch_time))
                with open('log/train.txt', 'a') as f:
                    f.write( 'train: {} @ epoch:{}/{} loss: {:.4f} cls_loss: {:.4f} cls_pos_loss: {:.4f} cls_neg_loss: {:.4f} forward time: {:.4f} batch time: {:.4f}'.format(counter,epoch, epochs, ret[0], ret[1], ret[2], ret[3], forward_time, batch_time))

                #print(counter, summary_interval, counter % summary_interval)
                if counter % summary_interval == 0:
                    print("summary_interval now")
                    summary_writer.add_summary(ret[-1], global_counter)

                #print(counter, summary_val_interval, counter % summary_val_interval)
                if counter % summary_val_interval == 0:
                    print("summary_val_interval now")
                    batch = sample_test_data(val_dir, bs * cfg.GPU_USE_COUNT, multi_gpu_sum=cfg.GPU_USE_COUNT)

                    ret = model.validate_step(sess, batch, summary=True)
                    summary_writer.add_summary(ret[-1], global_counter)

                    try:
                        ret = model.predict_step(sess, batch, summary=True)
                        summary_writer.add_summary(ret[-1], global_counter)
                    except:
                        print("prediction skipped due to error")

                if check_if_should_pause(tag):
                    model.saver.save(sess, os.path.join(save_model_dir, 'checkpoint'), global_step=model.global_step)
                    print('pause and save model @ {} steps:{}'.format(save_model_dir, model.global_step.eval()))
                    sys.exit(0)

                batch_time = time.time()
#             experiment.log_epoch_end(epoch)
            sess.run(model.epoch_add_op)

            model.saver.save(sess, os.path.join(save_model_dir, 'checkpoint'), global_step=model.global_step)

            # dump test data every 10 epochs
            if ( epoch + 1 ) % 10 == 0:
                # create output folder
                os.makedirs(os.path.join(output_path, str(epoch)), exist_ok=True)
                os.makedirs(os.path.join(output_path, str(epoch), 'data'), exist_ok=True)
                if vis:
                    os.makedirs(os.path.join(output_path, str(epoch), 'vis'), exist_ok=True)

                for batch in iterate_data(val_dir, shuffle=False, aug=False, is_testset=False, batch_size=bs * cfg.GPU_USE_COUNT, multi_gpu_sum=cfg.GPU_USE_COUNT):

                    if vis:
                        tags, results, front_images, bird_views, heatmaps = model.predict_step(sess, batch, summary=False, vis=True)
                    else:
                        tags, results = model.predict_step(sess, batch, summary=False, vis=False)

                    for tag, result in zip(tags, results):
                        of_path = os.path.join(output_path, str(epoch), 'data', tag + '.txt')
                        with open(of_path, 'w+') as f:

                            labels = box3d_to_label([result[:, 1:8]], [result[:, 0]], [result[:, -1]], coordinate='lidar')[0]
                            for line in labels:
                                f.write(line)
                            print('write out {} objects to {}'.format(len(labels), tag))
                    # dump visualizations
                    if vis:
                        for tag, front_image, bird_view, heatmap in zip(tags, front_images, bird_views, heatmaps):
                            front_img_path = os.path.join( output_path, str(epoch),'vis', tag + '_front.jpg'  )
                            bird_view_path = os.path.join( output_path, str(epoch), 'vis', tag + '_bv.jpg'  )
                            heatmap_path = os.path.join( output_path, str(epoch), 'vis', tag + '_heatmap.jpg'  )
                            cv2.imwrite( front_img_path, front_image )
                            cv2.imwrite( bird_view_path, bird_view )
                            cv2.imwrite( heatmap_path, heatmap )

                # execute evaluation code
                cmd_1 = "./kitti_eval/launch_test.sh"
                cmd_2 = os.path.join( output_path, str(epoch) )
                cmd_3 = os.path.join( output_path, str(epoch), 'log' )
                os.system( " ".join( [cmd_1, cmd_2, cmd_3] ) )



        print('train done. total epoch:{} iter:{}'.format(
            epoch, model.global_step.eval()))

        # finallly save model
        model.saver.save(sess, os.path.join(
            save_model_dir, 'checkpoint'), global_step=model.global_step)


INFO:tensorflow:Summary name Variable:0 is illegal; using Variable_0 instead.
INFO:tensorflow:Summary name Variable_1:0 is illegal; using Variable_1_0 instead.
INFO:tensorflow:Summary name Variable_2:0 is illegal; using Variable_2_0 instead.
INFO:tensorflow:Summary name VFE-1/kernel:0 is illegal; using VFE-1/kernel_0 instead.
INFO:tensorflow:Summary name VFE-1/bias:0 is illegal; using VFE-1/bias_0 instead.
INFO:tensorflow:Summary name VFE-1/gamma:0 is illegal; using VFE-1/gamma_0 instead.
INFO:tensorflow:Summary name VFE-1/beta:0 is illegal; using VFE-1/beta_0 instead.
INFO:tensorflow:Summary name VFE-1/moving_mean:0 is illegal; using VFE-1/moving_mean_0 instead.
INFO:tensorflow:Summary name VFE-1/moving_variance:0 is illegal; using VFE-1/moving_variance_0 instead.
INFO:tensorflow:Summary name VFE-2/kernel:0 is illegal; using VFE-2/kernel_0 instead.
INFO:tensorflow:Summary name VFE-2/bias:0 is illegal; using VFE-2/bias_0 instead.
INFO:tensorflow:Summary name VFE-2/gamma:0 is illegal; u

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



train ['aug_005373_3_1_0375' 'aug_002122_1_312' 'aug_002317_2_0_5377'
 'aug_001796_3_0_9882']
train: 741 @ epoch:3/160 loss: 0.9592 cls_loss: 0.2329 cls_pos_loss: 0.4348 cls_neg_loss: 0.0621 forward time: 0.9677 batch time: 1.3614
train ['aug_002256_1_312' 'aug_000522_3_0_9736' 'aug_002190_3_1_0017'
 'aug_001029_3_1_0057']
train: 742 @ epoch:3/160 loss: 0.5433 cls_loss: 0.2068 cls_pos_loss: 0.1721 cls_neg_loss: 0.0819 forward time: 0.9493 batch time: 1.2736
train ['aug_006657_3_1_0473' 'aug_002768_1_694' 'aug_002464_1_578'
 'aug_004478_2_-0_4887']
train: 743 @ epoch:3/160 loss: 1.3064 cls_loss: 0.2769 cls_pos_loss: 0.5825 cls_neg_loss: 0.0656 forward time: 0.9480 batch time: 1.2571
train ['aug_001692_2_-0_3853' 'aug_000064_1_851' 'aug_002053_3_0_9803'
 'aug_006728_3_1_0076']
train: 744 @ epoch:3/160 loss: 0.9553 cls_loss: 0.1742 cls_pos_loss: 0.1513 cls_neg_loss: 0.0682 forward time: 0.9418 batch time: 1.3674
train ['aug_004409_3_0_9933' 'aug_004579_2_0_6864' 'aug_002897_2_-0_1242'
 'a

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



train: 554 @ epoch:11/160 loss: 0.7710 cls_loss: 0.2130 cls_pos_loss: 0.5324 cls_neg_loss: 0.0399 forward time: 0.9772 batch time: 1.2916
train ['aug_001184_3_0_9533' 'aug_001607_3_1_0033' 'aug_001220_1_532'
 'aug_000502_1_207']
train: 555 @ epoch:11/160 loss: 0.6077 cls_loss: 0.1699 cls_pos_loss: 0.2218 cls_neg_loss: 0.0572 forward time: 1.0435 batch time: 1.4428
summary_interval now
train ['aug_002203_2_0_1103' 'aug_002435_2_-0_4966' 'aug_006189_2_-0_5990'
 'aug_006704_3_1_0402']
train: 556 @ epoch:11/160 loss: 0.5800 cls_loss: 0.2010 cls_pos_loss: 0.2796 cls_neg_loss: 0.0656 forward time: 0.9713 batch time: 1.3190
train ['aug_001950_3_0_9676' 'aug_000299_3_1_0263' 'aug_004025_1_44'
 'aug_001626_3_0_9689']
train: 557 @ epoch:11/160 loss: 0.4481 cls_loss: 0.1747 cls_pos_loss: 0.2344 cls_neg_loss: 0.0581 forward time: 0.9449 batch time: 1.3355
train ['aug_000652_1_900' 'aug_002855_2_0_1814' 'aug_004231_2_-0_4364'
 'aug_003846_3_0_9661']
train: 558 @ epoch:11/160 loss: 0.6908 cls_loss: 

...

train: 464 @ epoch:35/160 loss: 0.2045 cls_loss: 0.0489 cls_pos_loss: 0.0052 cls_neg_loss: 0.0238 forward time: 0.9927 batch time: 1.3231
train ['aug_004014_3_0_9873' 'aug_007101_3_0_9657' 'aug_001030_2_-0_3506'
 'aug_004417_3_1_0359']
train: 465 @ epoch:35/160 loss: 0.4140 cls_loss: 0.0848 cls_pos_loss: 0.0383 cls_neg_loss: 0.0376 forward time: 1.5804 batch time: 1.8979
summary_interval now
train ['aug_001623_3_1_0076' 'aug_005848_1_350' 'aug_002918_1_167'
 'aug_006776_1_32']
train: 466 @ epoch:35/160 loss: 0.9957 cls_loss: 0.2869 cls_pos_loss: 0.9646 cls_neg_loss: 0.0229 forward time: 1.0138 batch time: 1.3967
train ['aug_005541_2_0_5797' 'aug_005564_1_788' 'aug_004231_3_1_0175'
 'aug_004159_3_0_9661']
train: 467 @ epoch:35/160 loss: 0.7043 cls_loss: 0.0555 cls_pos_loss: 0.0616 cls_neg_loss: 0.0200 forward time: 0.9486 batch time: 1.3117
train ['aug_003911_1_778' 'aug_001648_1_830' 'aug_006933_3_0_9520'
 'aug_000041_2_-0_0452']
train: 468 @ epoch:35/160 loss: 0.2816 cls_loss: 0.0747 

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



train: 724 @ epoch:39/160 loss: 0.5820 cls_loss: 0.2804 cls_pos_loss: 0.9715 cls_neg_loss: 0.0188 forward time: 0.9331 batch time: 1.2436
train ['aug_000056_1_962' 'aug_004253_1_566' 'aug_004757_3_0_9792'
 'aug_002990_3_1_0370']
train: 725 @ epoch:39/160 loss: 0.1852 cls_loss: 0.0850 cls_pos_loss: 0.0098 cls_neg_loss: 0.0413 forward time: 0.9936 batch time: 1.1963
summary_interval now
train ['aug_005946_3_1_0310' 'aug_006248_2_0_6571' 'aug_007020_2_-0_2823'
 'aug_001876_3_1_0067']
train: 726 @ epoch:39/160 loss: 0.6024 cls_loss: 0.2480 cls_pos_loss: 0.6698 cls_neg_loss: 0.0403 forward time: 0.9746 batch time: 1.2841
train ['aug_004975_3_0_9572' 'aug_000977_3_1_0101' 'aug_006090_1_426'
 'aug_007237_3_0_9773']
train: 727 @ epoch:39/160 loss: 0.7669 cls_loss: 0.2369 cls_pos_loss: 0.6759 cls_neg_loss: 0.0339 forward time: 1.7728 batch time: 2.0715
train ['aug_004824_3_0_9846' 'aug_000574_1_190' 'aug_004584_3_1_0495'
 'aug_000442_1_236']
train: 728 @ epoch:39/160 loss: 0.7971 cls_loss: 0.13

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



train ['aug_000146_1_914' 'aug_002779_2_0_3876' 'aug_007129_1_612'
 'aug_005146_2_-0_0252']
train: 801 @ epoch:45/160 loss: 0.3822 cls_loss: 0.3011 cls_pos_loss: 0.8680 cls_neg_loss: 0.0421 forward time: 0.9538 batch time: 1.3439
train ['aug_002192_3_0_9860' 'aug_005824_2_0_3355' 'aug_000965_3_1_0177'
 'aug_004378_2_-0_7374']
train: 802 @ epoch:45/160 loss: 0.4052 cls_loss: 0.1045 cls_pos_loss: 0.1472 cls_neg_loss: 0.0338 forward time: 0.9399 batch time: 1.2685
train ['aug_005964_1_835' 'aug_000280_2_0_5416' 'aug_006015_2_0_1073'
 'aug_001414_1_885']
train: 803 @ epoch:45/160 loss: 0.6564 cls_loss: 0.1008 cls_pos_loss: 0.0442 cls_neg_loss: 0.0449 forward time: 0.9570 batch time: 1.3912
train ['aug_002918_2_-0_5516' 'aug_006557_1_718' 'aug_000136_3_1_0349'
 'aug_000041_1_451']
train: 804 @ epoch:45/160 loss: 3.6916 cls_loss: 0.6064 cls_pos_loss: 2.0556 cls_neg_loss: 0.0463 forward time: 1.5693 batch time: 1.8633
train ['aug_002734_1_840' 'aug_003803_1_713' 'aug_004601_3_1_0327'
 'aug_00